In [373]:
import numpy as np
from random import randint
from math import floor, fabs
from cplex.callbacks import UserCutCallback
import cplex  as CPX
import cplex.callbacks as CPX_CB
import sys

def SecModelParameter ( VarsValue, m, n, my_rhs, my_coef, BranchedVariables):
    print 'BranchedVariables',BranchedVariables
    unbranched=list()
    c=[]
    d=(np.zeros(((2 * m) + (4 * n), 2*n)))
    halatest=[]
    a=[]
    newrow=[]
    zer=(np.zeros(((2 * m) + (4 * n), 2*n)))
    for i in range (n):
        if i not in (BranchedVariables):
            unbranched.append(i)
    NodeNum=n-len(unbranched)
    
    
    for i in unbranched:   
        for h in range (m):
            c.append(0)
        for h in range (m):
            lin=0            
            for j in range (n):
#                 print 'i', i, 'h', h,'j',j
#                 print 'j1',j
                if j in (BranchedVariables):
#                     print 'j2',j
                    sv = VarsValue[BranchedVariables.index(j)]
#                     print 'sv', sv
                    lin =lin+ (sv * my_coef[h][j]) 
#                     print 'lin', lin
#                 print 'sv'
            lin=lin- my_rhs[h]
            c.append(lin)                
        for h in range (n):
            c.append(0)
        for h in range (n):
            c.append(0)

        for jj in range (n):
            lin2=-1
            if jj in (BranchedVariables):
                sv = VarsValue[BranchedVariables.index(jj)]
                lin2 =lin2+ sv
            c.append(lin2)
            
        for jj in range (n):
            lin2=0
            if jj in (BranchedVariables):
                lin2 =-1*VarsValue[BranchedVariables.index(jj)]
            c.append(lin2)

              
    k=NodeNum-1 

    for i in unbranched: 
        k=k+1
        for t in range(m):              
            for j in range(n):    
                d[(k-NodeNum)*(2*m+4*n)+t][j+n]=my_coef[t][j] 
                
        for t in range(m):  
            d[(k-NodeNum)*(2*m+4*n)+t][n+i]=d[(k-NodeNum)*(2*m+4*n)+t][n+i]-my_rhs[t]   
                
        for t in range(m):  
            for kk in unbranched:
                d[(k-NodeNum)*(2*m+4*n)+t+m][kk]=my_coef[t][kk] 
                

        for t in range(m):  
            for j in range(n):
                d[(k-NodeNum)*(2*m+4*n)+t+m][j+n]=-1*my_coef[t][j] 
                 
        for t in range(m):  
            d[(k-NodeNum)*(2*m+4*n)+t+m][n+i]=d[(k-NodeNum)*(2*m+4*n)+t+m][n+i]+my_rhs[t] 
                
        for t in range(n):              
            d[(k-NodeNum)*(2*m+4*n)+t+2*m][i]=-1 
            
        for t in range(n):  
            
            d[(k-NodeNum)*(2*m+4*n)+2*m+t][n+t]=1 
        
            
        for t in range(n):  
            
            d[(k-NodeNum)*(2*m+4*n)+2*m+n+t][n+t]=-1 
        
        for mm in unbranched: 
             
            d[(k-NodeNum)*(2*m+4*n)+2*m+2*n+mm][mm]=1  
            
        for t in range(n):  
            
            d[(k-NodeNum)*(2*m+4*n)+t+2*n+2*m][i]=d[(k-NodeNum)*(2*m+4*n)+t+2*n+2*m][i]+1            
            

        for t in range(n):  
            
            d[(k-NodeNum)*(2*m+4*n)+2*m+2*n+t][n+t]=-1 

        for t in unbranched:  
            d[(k-NodeNum)*(2*m+4*n)+2*m+3*n+t][t]=-1  
               
        
        for t in range(n):  
            
            d[(k-NodeNum)*(2*m+4*n)+2*m+3*n+t][n+t]=1 
            
        d=np.vstack([d, zer])                          
            
    d = np.delete(d, slice(((n - NodeNum)*((2 * m) + (4 * n))),((n-NodeNum+1)*((2 * m) + (4 * n)))), axis=0)
#     print 'c',c
#     print 'unbranched',unbranched
    return c, d,unbranched
    print c, d,unbranched

In [374]:
def SecondModel (cc,dd,NotBranched):
#     print 'cc,dd,NotBranched',cc,dd,NotBranched
    numrows = len(dd)    # 3 rows in your example
    numcols = len(dd[0])
    VarNum=numcols/2
    ConstNum=numrows/len(NotBranched)
    my_obj=[]
    my_ub=[]
    my_lb=[]
    my_colnames=[]
    my_rownames=["c1"]
    my_coef=[] 
    my_row=[]
    my_rhs=[]
    my_sense=""
    my_Nmah=list()
    
    for i in range(numrows):
        my_obj=cc
        my_ub.append(1)
        my_lb.append(0)
        my_colnames.append("y"+str(i))

    sumarray=[]     
    NotBranched.sort()    
#     sumshode=list()
    for t in range (VarNum):
        sumlist=list()
        for j in range(numrows):
#             print 't,j',t,j
            if t in NotBranched: 
                indj=NotBranched.index(t)
#                 print 'indj',indj
                indjrange=range(indj*ConstNum,(indj+1)*ConstNum)
#                 print 'indjrange',indjrange
                if j in indjrange:
#                     print 'dd[j,t]+dd[j,t+VarNum]',j,'ll',dd[j,t]+dd[j,t+VarNum]
                    sumlist.append(dd[j,t]+dd[j,t+VarNum])
                    dd[j,t+VarNum]=0
                else:
                    sumlist.append(dd[j,t])
            else:
                sumlist.append(dd[j,t])
        sumarray.append(sumlist)
#     print 'sumarray',sumarray
#     print 'newDD',dd
  
#     print 'notbranched',NotBranched
    lenNotbranched=len(NotBranched)
   
    
    for t in range(lenNotbranched):  
        for i in range (VarNum):
            sumlist=list()
            if t>0:
                for p in range(t):
                    for j in range (ConstNum):
                        sumlist.append(0) 
                        
            for j in range(ConstNum):
                sumlist.append(dd[t*ConstNum+j,i+VarNum])
            if i in NotBranched and i > NotBranched[t]:
                indx=NotBranched.index(i)
                indy=NotBranched[t]
                
                for x in range(indx-indy-1):
                    for j in range (ConstNum):
                        sumlist.append(0) 
                for j in range(ConstNum):
                    sumlist.append(dd[(indx)*ConstNum+j,indy+VarNum])
                    dd[(indx)*ConstNum+j,indy+VarNum]=0
#                 sumarray.append([t+indx,indy])
                if t<lenNotbranched-2 :
                    for p in range(lenNotbranched-indx-1):
                        for j in range (ConstNum):
                            sumlist.append(0)
            else:
                if t<lenNotbranched-1 :
#                     print 'lenNotbranched',lenNotbranched
                    for p in range(lenNotbranched-t-1):
                            for j in range (ConstNum):
                                sumlist.append(0) 
#             print 't,i',t,',',i
#             print 'sumlist p2',sumlist
#             print 'lensumlist p2',len(sumlist)
            sumarray.append(sumlist)
#     print 'part2' ,sumarray  
    
    rows=[]
    for j in range(numrows):
        my_row.append(1)
    rows.append([range(numrows),my_row])  
    def populatebyrow(SecProb):
        SecProb.objective.set_sense(SecProb.objective.sense.maximize)
        SecProb.variables.add(obj = my_obj,lb=my_lb, names = my_colnames)
        
        for i in range (len(sumarray)):
            if all(k == 0 for k in sumarray[i])!=True:
#                 print 'i',i
                sumline=[]
                sumline.append([range(len(sumarray[i])),sumarray[i]])
#                 print 'sumline',sumline
                SecProb.linear_constraints.add(lin_expr = sumline, senses =  "E",
                                rhs = [0], names = ["u"+str(i)])
        SecProb.linear_constraints.add(lin_expr = rows, senses = "L",
                                             rhs = [1], names = ["t0"])
    
    my_SecProb = CPX.Cplex()
    handle = populatebyrow(my_SecProb)
    my_SecProb.solve()
    my_SecProb.write("lpex2.lp")
    SecVariables    = my_SecProb.solution.get_values()
    SecObjective=my_SecProb.solution.get_objective_value()
#     print 'SecVariables,SecObjective,my_colnames',SecVariables, SecObjective,my_colnames
    return SecVariables, SecObjective,my_colnames

In [375]:
def GeneratintCutParameters ( m, n, my_rhs, my_coef, BranchedVariables,SecVariables): 
    BranchedLen=len(BranchedVariables)
    lhs=(np.zeros(((2 * m) + (4 * n),BranchedLen)))
    zer=(np.zeros(((2 * m) + (4 * n), BranchedLen)))
    rhs=(np.zeros(((2 * m) + (4 * n),1)))
#     print rhs
    zerRhs=(np.zeros(((2 * m) + (4 * n), 1)))

    unbranched=list()
    for i in range (n):
        if i not in (BranchedVariables):
            unbranched.append(i)  
                        
    NodeNum=n-len(unbranched)
    k=NodeNum-1    
    
    for i in unbranched:   
        k=k+1
        for h in range (m):
            for j in range (n):
                if j in (BranchedVariables):
                    lhs[(k-NodeNum)*(2*m+4*n)+m+h][BranchedVariables.index(j)]=my_coef[h][j]*SecVariables[(k-NodeNum)*(2*m+4*n)+m+h]  
                    rhs[(k-NodeNum)*(2*m+4*n)+m+h]=my_rhs[h]*SecVariables[(k-NodeNum)*(2*m+4*n)+m+h]  
            
#         for h in range (n):
        for j in range (n):
            if j in (BranchedVariables):
                lhs[(k-NodeNum)*(2*m+4*n)+2*m+2*n+j][BranchedVariables.index(j)]=SecVariables[(k-NodeNum)*(2*m+4*n)+2*m+2*n+j]  
                rhs[(k-NodeNum)*(2*m+4*n)+m+h]=SecVariables[(k-NodeNum)*(2*m+4*n)+m+h]  
            
#         for h in range (n):
        for j in range (n):
            if j in (BranchedVariables):
                lhs[(k-NodeNum)*(2*m+4*n)+2*m+3*n+j][BranchedVariables.index(j)]=-1*SecVariables[(k-NodeNum)*(2*m+4*n)+2*m+3*n+j]  
                                                                            
        lhs=np.vstack([lhs, zer]) 
        rhs=np.vstack([rhs, zerRhs])   
    lhs = np.delete(lhs, slice(((n - NodeNum)*((2 * m) + (4 * n))),((n-NodeNum+1)*((2 * m) + (4 * n)))), axis=0)
    rhs = np.delete(rhs, slice(((n - NodeNum)*((2 * m) + (4 * n))),((n-NodeNum+1)*((2 * m) + (4 * n)))), axis=0)
    FinalLhs=np.sum(lhs, axis=0)
    FinalRhs=np.sum(rhs, axis=0)
#     print 'SecVariables[(k-NodeNum)*(2*m+4*n)+m+h]',SecVariables[182]
    print FinalLhs
    print FinalRhs
    return FinalLhs,FinalRhs
#     print lhs, rhs

In [376]:
class MyCut(CPX_CB.UserCutCallback):

    def __call__(self):
         
        self.times_called += 1
#         print  'self.times_called', self.times_called
        branched=list()
        values=list()
        branchedNames=list()
        senses= "L"
        print 'get_num_nodes', self.get_num_nodes()

#         print 'self.get_lower_bounds(s)',self.get_lower_bounds()
#         print 'self.get_upper_bounds(s)',self.get_upper_bounds()
#         print 'objective value', self.get_objective_value()
#         print 'values', self.get_values()
        lb=self.get_lower_bounds()
        ub=self.get_upper_bounds()               
        for j in range(len(lb)):
            if lb[j]==ub[j]:
                branched.append(j)
                values.append(lb[j])
                branchedNames.append(VarsName[j])
#         print 'values',values
#         print 'branchedNames',branchedNames
#         print 'branched',branched
#         if len(values)>0:
#             SecModelParameterOutput=SecModelParameter(values, self.m, self.n, self.my_rhs, self.my_coef,branched)
#             SecondModelOutput=SecondModel (SecModelParameterOutput[0],SecModelParameterOutput[1],SecModelParameterOutput[2])
#             print 'SecondModelOutput[1]',SecondModelOutput[1]
#             print 'SecondModelOutput[0]',SecondModelOutput[0]
#             if SecondModelOutput[1]>0.000000000001:
#                 print 'bayad cut bezane'
#                 output=GeneratintCutParameters (self.m, self.n, self.my_rhs, self.my_coef,branched, SecondModelOutput[0])
#                 print 'output',output[0]
#                 print 'output[1]',output[1]
#                 lhs=[CPX.SparsePair(ind =branchedNames, val = output[0])]
#                 print 'lhs',lhs[0]
#                 self.add(cut=lhs[0],rhs=output[1][0],sense=senses)
#                 print 'cut added'


In [377]:
my_obj=[]
my_ub=[]
my_lb=[]
my_colnames=[]
my_vtype =""
my_rhs=[]
my_rownames=[]
my_coef=[] 
rows=[]
my_sense=""
m=500
n=60

for i in range(n):
    my_obj.append(randint(1,100))
    my_ub.append(1)
    my_lb.append(0)
    my_colnames.append("x"+str(i))
    my_vtype=my_vtype+'I'
    
for i in range(m):
#     my_rhs.append(randint(1,10))
    my_rownames.append("c"+str(i))
    my_row=[]
    for j in range(n):
        my_row.append(randint(-100,100))
    my_coef.append(my_row)
    rows.append([range(n),my_coef[i]])  
    my_sense=my_sense+'L'
PositiveMatrix=[]    
for i in range (m):
    if np.max(my_coef[i][:]) < 0:
         PositiveMatrix.append(10)
    else:
        x = 0
        for j in range (n):
            if my_coef[i][j] > 0:
                x+=my_coef[i][j]
        PositiveMatrix.append(x)

for i in range(m):
    my_rhs.append(randint(0,(PositiveMatrix[i])))
    
def populatebyrow(c):
    c.objective.set_sense(c.objective.sense.maximize)
    # since lower bounds are all 0.0 (the default), lb is omitted here
    c.variables.add(obj = my_obj, ub = my_ub,lb=my_lb, types = my_vtype, names = my_colnames)
    c.linear_constraints.add(lin_expr = rows, senses = my_sense,
                                rhs = my_rhs, names = my_rownames)

In [ ]:
def admipex3(c):
    
    c.parameters.preprocessing.presolve = 0

    c.parameters.preprocessing.reduce = 0

    c.parameters.preprocessing.linear.set(0)

    c.parameters.preprocessing.numpass = 0

    c.parameters.mip.strategy.presolvenode = -1

    c.parameters.preprocessing.linear = 0
    
def CutCplex(c):
    c.parameters.mip.cuts.disjunctive.set(-1)
    c.parameters.mip.cuts.bqp.set(-1)
    c.parameters.mip.cuts.cliques.set(-1)
    c.parameters.mip.cuts.covers.set(-1)
    c.parameters.mip.cuts.flowcovers.set(-1)
    c.parameters.mip.cuts.gomory.set(-1)
    c.parameters.mip.cuts.gubcovers.set(-1)
    c.parameters.mip.cuts.implied.set(-1)
    c.parameters.mip.cuts.liftproj.set(-1)
    c.parameters.mip.cuts.localimplied.set(-1)
    c.parameters.mip.cuts.mcfcut.set(-1)
    c.parameters.mip.cuts.mircut.set(-1)
    c.parameters.mip.cuts.zerohalfcut.set(-1)
    c.parameters.mip.cuts.pathcut.set(-1)
    
c = CPX.Cplex()
populatebyrow(c)
admipex3(c)
    
c.set_log_stream(sys.stdout)
c.set_results_stream(sys.stdout)


CutCplex(c)
VarsName=c.variables.get_names()
c.set_log_stream(sys.stdout)
c.set_results_stream(sys.stdout)

cutinst=c.register_callback(MyCut)
cutinst.times_called = 0
cutinst.m=m
cutinst.n=n
cutinst.my_rhs=my_rhs
cutinst.my_coef=my_coef
cutinst.VarsName=VarsName
c.parameters.mip.interval.set(1)
c.parameters.preprocessing.linear=0
c.parameters.mip.strategy.search.set(c.parameters.mip.strategy.search.values.traditional)
c.write("NewExample.lp")
c.solve()
solution = c.solution

# the following line prints the corresponding string
print solution.status[solution.get_status()]
print "Objective value = " , solution.get_objective_value()
print
x = solution.get_values(0, c.variables.get_num()-1)
for j in range(c.variables.get_num()):
    if fabs(x[j]) > 1.0e-10:
        print "Column %d: Value = %17.10g" % (j, x[j])

print "Cut callback was called ", cutinst.times_called, "times"


CPXPARAM_Read_DataCheck                          1
CPXPARAM_Preprocessing_Linear                    0
CPXPARAM_MIP_Cuts_Cliques                        -1
CPXPARAM_MIP_Cuts_Covers                         -1
CPXPARAM_MIP_Interval                            1
CPXPARAM_MIP_Cuts_FlowCovers                     -1
CPXPARAM_MIP_Cuts_Implied                        -1
CPXPARAM_MIP_Cuts_GUBCovers                      -1
CPXPARAM_MIP_Cuts_Gomory                         -1
CPXPARAM_MIP_Cuts_PathCut                        -1
CPXPARAM_MIP_Cuts_MIRCut                         -1
CPXPARAM_MIP_Cuts_Disjunctive                    -1
CPXPARAM_MIP_Strategy_Search                     1
CPXPARAM_MIP_Cuts_ZeroHalfCut                    -1
CPXPARAM_MIP_Cuts_MCFCut                         -1
CPXPARAM_MIP_Cuts_LiftProj                       -1
CPXPARAM_MIP_Cuts_LocalImplied                   -1
CPXPARAM_MIP_Cuts_BQP                            -1
Found incumbent of value 0.000000 after 0.00 sec. (0.01 ticks)
Tried

get_num_nodes 39
     39    35     1335.1668    20        0.0000     1549.9428      710     ---              x58 U     39     36     12
get_num_nodes 40
get_num_nodes 40
     40    36     1399.8466    23        0.0000     1549.9428      720     ---               x1 U     40     38     13
Elapsed time = 1.09 sec. (367.69 ticks, tree = 0.03 MB, solutions = 1)
get_num_nodes 41
get_num_nodes 41
     41    37     1396.3953    24        0.0000     1549.9428      724     ---              x37 U     41     40     14
get_num_nodes 42
get_num_nodes 42
     42    38     1347.4219    22        0.0000     1549.9428      735     ---               x9 U     42     41     15
get_num_nodes 43
get_num_nodes 43
     43    39     1298.4938    21        0.0000     1549.9428      748     ---               x9 D     43     41     15
get_num_nodes 44
get_num_nodes 44
     44    40     1318.8671    23        0.0000     1549.9428      758     ---              x35 D     44     42     16
     45    39        cutoff 

     91    74     1458.2949    22        0.0000     1548.5753     1293     ---              x19 U     91     90     17
get_num_nodes 92
get_num_nodes 92
     92    75     1409.8264    20        0.0000     1548.5753     1314     ---              x41 D     92     91     18
get_num_nodes 93
get_num_nodes 93
     93    76     1408.5504    20        0.0000     1548.5753     1316     ---              x29 U     93     92     19
get_num_nodes 94
get_num_nodes 94
     94    77     1404.5809    21        0.0000     1548.5753     1320     ---               x2 D     94     93     20
get_num_nodes 95
get_num_nodes 95
     95    78     1391.9788    19        0.0000     1548.5753     1327     ---              x18 D     95     94     21
get_num_nodes 96
get_num_nodes 96
     96    79     1366.1195    16        0.0000     1548.5753     1332     ---              x39 U     96     95     22
get_num_nodes 97
get_num_nodes 97
     97    80     1339.5874    18        0.0000     1548.5753     1337     ---    

    143   115     1102.7053    24        0.0000     1540.0112     2064     ---              x19 D    143    140     17
get_num_nodes 144
get_num_nodes 144
    144   116     1234.6076    22        0.0000     1540.0112     2068     ---               x2 D    144    142     18
get_num_nodes 145
get_num_nodes 145
    145   117     1104.4323    20        0.0000     1540.0112     2098     ---              x57 U    145    144     19
get_num_nodes 146
get_num_nodes 146
    146   118     1224.9203    21        0.0000     1540.0112     2102     ---              x57 D    146    144     19
get_num_nodes 147
get_num_nodes 147
    147   119     1217.1335    19        0.0000     1540.0112     2107     ---              x21 D    147    146     20
    148   118    infeasible              0.0000     1540.0112     2136     ---              x38 D    148    147     21
get_num_nodes 149
get_num_nodes 149
    149   119     1183.2458    20        0.0000     1540.0112     2145     ---              x38 U    149  

    195   151     1249.2468    18        0.0000     1539.1134     2657     ---              x52 U    195    194     20
    196   150    infeasible              0.0000     1539.1134     2678     ---               x2 D    196    195     21
    197   149    infeasible              0.0000     1539.1134     2691     ---               x2 U    197    195     21
get_num_nodes 198
get_num_nodes 198
    198   150     1473.7321    34        0.0000     1539.0312     2720     ---              x32 D    198     25      3
get_num_nodes 199
get_num_nodes 199
    199   151     1462.5798    33        0.0000     1539.0312     2733     ---              x42 U    199    198      4
get_num_nodes 200
get_num_nodes 200
    200   152     1412.9996    28        0.0000     1539.0312     2754     ---              x34 U    200    199      5
Elapsed time = 3.44 sec. (570.13 ticks, tree = 0.04 MB, solutions = 1)
get_num_nodes 201
get_num_nodes 201
    201   153     1336.3504    25        0.0000     1539.0312     2785 

...

  27263 14937     1205.1397    28        0.0000     1329.5627   363763     ---              x19 D  27263  27262     14
get_num_nodes 27264
get_num_nodes 27264
  27264 14938     1186.0820    27        0.0000     1329.5627   363783     ---              x57 U  27264  27263     15
get_num_nodes 27265
get_num_nodes 27265
  27265 14939     1138.2839    28        0.0000     1329.5627   363816     ---              x57 D  27265  27263     15
get_num_nodes 27266
get_num_nodes 27266
  27266 14940     1172.7537    28        0.0000     1329.5627   363825     ---               x1 U  27266  27264     16
get_num_nodes 27267
get_num_nodes 27267
  27267 14941     1110.1282    25        0.0000     1329.5627   363853     ---              x59 U  27267  27266     17
get_num_nodes 27268
get_num_nodes 27268
  27268 14942     1004.5530    22        0.0000     1329.5627   363864     ---              x30 D  27268  27267     18
get_num_nodes 27269
get_num_nodes 27269
  27269 14943      963.6685    20        0.000

  27315 14965     1267.4385    30        0.0000     1329.5328   364407     ---               x9 D  27315  27314     14
get_num_nodes 27316
get_num_nodes 27316
  27316 14966     1257.4212    27        0.0000     1329.5328   364418     ---              x14 D  27316  27315     15
get_num_nodes 27317
get_num_nodes 27317
  27317 14967     1173.2560    25        0.0000     1329.5328   364458     ---              x14 U  27317  27315     15
get_num_nodes 27318
get_num_nodes 27318
  27318 14968     1137.1763    26        0.0000     1329.5328   364473     ---              x57 U  27318  27317     16
  27319 14967    infeasible              0.0000     1329.5328   364475     ---              x34 D  27319  27318     17
  27320 14966    infeasible              0.0000     1329.5328   364482     ---              x34 U  27320  27318     17
Elapsed time = 361.42 sec. (28505.55 ticks, tree = 3.75 MB, solutions = 1)
get_num_nodes 27321
get_num_nodes 27321
  27321 14967     1323.2052    26        0.0000    

  27367 14991     1248.9315    23        0.0000     1329.3927   365153     ---              x41 D  27367  27366     14
get_num_nodes 27368
get_num_nodes 27368
  27368 14992     1220.7741    20        0.0000     1329.3927   365163     ---              x32 U  27368  27367     15
get_num_nodes 27369
get_num_nodes 27369
  27369 14993     1114.5223    23        0.0000     1329.3927   365184     ---               x1 U  27369  27368     16
  27370 14992    infeasible              0.0000     1329.3927   365194     ---               x9 D  27370  27369     17
Elapsed time = 362.09 sec. (28559.33 ticks, tree = 3.76 MB, solutions = 1)
  27371 14991    infeasible              0.0000     1329.3927   365198     ---               x9 U  27371  27369     17
get_num_nodes 27372
get_num_nodes 27372
  27372 14992     1278.5698    22        0.0000     1329.3758   365215     ---              x21 U  27372  18755     16
get_num_nodes 27373
get_num_nodes 27373
  27373 14993     1247.0314    22        0.0000    

  27419 15017    infeasible              0.0000     1329.3465   365850     ---               x9 D  27419  27417     22
  27420 15016        cutoff              0.0000     1329.3465   365862     ---               x9 U  27420  27417     22
Elapsed time = 362.75 sec. (28613.70 ticks, tree = 3.76 MB, solutions = 1)
get_num_nodes 27421
get_num_nodes 27421
  27421 15017     1299.7457    25        0.0000     1329.3257   365879     ---               x2 U  27421  17189     13
get_num_nodes 27422
get_num_nodes 27422
  27422 15018     1270.6319    28        0.0000     1329.3257   365893     ---              x19 D  27422  27421     14
get_num_nodes 27423
get_num_nodes 27423
  27423 15019     1240.2180    26        0.0000     1329.3257   365914     ---              x14 D  27423  27422     15
get_num_nodes 27424
get_num_nodes 27424
  27424 15020     1238.9636    25        0.0000     1329.3257   365921     ---              x37 U  27424  27423     16
get_num_nodes 27425
get_num_nodes 27425
  27425 150

  27471 15043     1069.5994    20        0.0000     1329.2753   366477     ---              x48 D  27471  27470     24
get_num_nodes 27472
get_num_nodes 27472
  27472 15044     1067.2558    19        0.0000     1329.2753   366480     ---              x45 U  27472  27471     25
get_num_nodes 27473
get_num_nodes 27473
  27473 15045     1040.3731    19        0.0000     1329.2753   366487     ---              x18 D  27473  27472     26
get_num_nodes 27474
get_num_nodes 27474
  27474 15046     1024.3427    20        0.0000     1329.2753   366495     ---              x14 U  27474  27473     27
get_num_nodes 27475
get_num_nodes 27475
  27475 15047     1023.4223    17        0.0000     1329.2753   366500     ---              x59 U  27475  27474     28
get_num_nodes 27476
get_num_nodes 27476
  27476 15048      996.9577    14        0.0000     1329.2753   366507     ---              x58 D  27476  27475     29
get_num_nodes 27477
get_num_nodes 27477
  27477 15049      993.0274    13        0.000